In [11]:
#Feature Extraction
import numpy as np
import glob
import math
import scipy
from scipy.spatial import distance
from scipy import signal
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics


#modulating function as defined in paper
def m(x ,y, f):
    val = np.cos(2*np.pi*f*math.sqrt(x **2 + y**2))
    return val
#spatial filter as defined in paper
def gabor(x, y, dx, dy, f):
    gb = (1/(2*math.pi*dx*dy))*np.exp(-0.5*(x**2 / dx**2 + y**2 / dy**2)) * m(x, y, f)
    return gb

#function to calculate spatial filter over 8x8 blocks
def spatial(f,dx,dy):
    sfilter=np.zeros((8,8))
    for i in range(8):
        for j in range(8):
            sfilter[i,j]=gabor((-4+j),(-4+i),dx,dy,f)
    return sfilter

def get_vec(convolvedtrain1,convolvedtrain2):
    feature_vec=[]
    for i in range(6):
            for j in range(64):
                #Run 8 by 8 filtered block iteratively over the entire image
                start_height = i*8
                end_height = start_height+8
                start_wid = j*8
                end_wid = start_wid+8
                grid1 = convolvedtrain1[start_height:end_height, start_wid:end_wid]
                grid2 = convolvedtrain2[start_height:end_height, start_wid:end_wid]

                # Channel 1
                absolute = np.absolute(grid1)
                # mean
                mean = np.mean(absolute)
                feature_vec.append(mean)
                #deviation
                std = np.mean(np.absolute(absolute-mean))
                feature_vec.append(std)

                # Channel 2
                absolute = np.absolute(grid2)
                # mean
                mean = np.mean(absolute)
                feature_vec.append(mean)
                #deviation
                std = np.mean(np.absolute(absolute-mean))
                feature_vec.append(std)

    return feature_vec

def FeatureExtraction(enhanced):
    con1=[]
    con2=[]
    #get spatial filters
    filter1=spatial(0.67,3,1.5)
    filter2=spatial(0.67,4,1.5) 
    
    feature_vector=[]
    
    for i in range(len(enhanced)):
        img=enhanced[i]
        #define a 48x512 region over which the filters are applied
        img_roi=img[:48,:]
        
        filtered1=scipy.signal.convolve2d(img_roi,filter1,mode='same')
        filtered2=scipy.signal.convolve2d(img_roi,filter2,mode='same')
        
        con1.append(filtered1)
        con2.append(filtered2)
        fv=get_vec(filtered1,filtered2)
        feature_vector.append(fv)
    return feature_vector #each feature vector has a dimension of 1536


In [12]:
#Image Enhancement
import cv2
import numpy as np
import glob
import math
from scipy.spatial import distance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics

#Equalizes the histogram of the image
def ImageEnhancement(normalized):
    enhanced=[]
    for res in normalized:
        res = res.astype(np.uint8)
        im=cv2.equalizeHist(res)
        enhanced.append(im)
    return enhanced


In [13]:
#Iris Localization
import cv2
import numpy as np
import glob
import math
from scipy.spatial import distance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics

def IrisLocalization(images):
    #convert image to a color image
    target = [cv2.cvtColor(img, cv2.COLOR_BGR2GRAY) for img in images]
    boundary=[] #initialize empty list that will eventually contain all the images with boundaries
    centers=[] #initialize empty list that will contain the centers of the boundary circles
    for img in target:
        
        draw_img=img
        
        # remove noise by blurring the image
        blur = cv2.bilateralFilter(img, 9,75,75)
        img=blur
        
        #estimate the center of pupil
        horizontalProjection = np.mean(img,0);
        verticalProjection = np.mean(img,1);
        center_x=horizontalProjection.argmin()
        center_y=verticalProjection.argmin()
        
        #recalculate of pupil by concentrating on a 120X120 area
        centrecrop_x = img[center_x-60:center_x+60]
        centrecrop_y = img[center_y-60:center_y+60]
        horizontalProjection = np.mean(centrecrop_y,0);
        verticalProjection = np.mean(centrecrop_x,0);
        crop_center_x=horizontalProjection.argmin()
        crop_center_y=verticalProjection.argmin()

        cimg=img.copy()
        cv2.circle(cimg,(crop_center_x,crop_center_y),1,(255,0,0),2)

        #apply Canny edge detector on the masked image
        maskimage = cv2.inRange(img, 0, 70)
        output = cv2.bitwise_and(img, maskimage)
        edged = cv2.Canny(output, 100, 220)
        
        # Apply Hough transform to find potential boundaries of pupil
        circles = cv2.HoughCircles(edged, cv2.HOUGH_GRADIENT, 10, 100)
        
        #define the center of the pupil
        a = (crop_center_x,crop_center_y)
        
        out = img.copy()
        min_dst=math.inf
        for i in circles[0]:
            #find the circle whose center is closest to the approx center found above
            b=(i[0],i[1])
            dst = distance.euclidean(a, b)
            if dst<min_dst:
                min_dst=dst
                k=i
                
        #draw the inner boundary
        cv2.circle(draw_img, (k[0], k[1]), k[2], (255, 0, 0), 3)

        pupil=circles[0][0]
        radius_pupil = int(k[2])
        
        #draw the outer boundary, which is approximately found to be at a distance 53 from the inner boundary 
        cv2.circle(draw_img, (k[0], k[1]), radius_pupil+53, (255, 0, 0), 3)
        boundary.append(draw_img)
        centers.append([k[0],k[1],k[2]])
    return boundary,centers



In [14]:
# coding: utf-8
#Iris Normalization
import cv2
import numpy as np
import glob
import math
from scipy.spatial import distance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics

def IrisNormalization(boundary,centers):
    target = [img for img in boundary]
    normalized=[]
    cent=0
    for img in target:
        #load pupil centers and radius of inner circles
        center_x = centers[cent][0]
        center_y = centers[cent][1]
        radius_pupil=int(centers[cent][2])
        
        iris_radius = 53 # width of space between inner and outer boundary
    
        #define equally spaced interval to iterate over
        nsamples = 360
        samples = np.linspace(0,2*np.pi, nsamples)[:-1]
        polar = np.zeros((iris_radius, nsamples))
        for r in range(iris_radius):
            for theta in samples:
                #get x and y for values on inner boundary
                x = (r+radius_pupil)*np.cos(theta)+center_x
                y = (r+radius_pupil)*np.sin(theta)+center_y
                x=int(x)
                y=int(y)
                try:
                #convert coordinates
                    polar[r][int((theta*nsamples)/(2*np.pi))] = img[y][x]
                except IndexError: #ignores values which lie out of bounds
                    pass
                continue
        res = cv2.resize(polar,(512,64))
        normalized.append(res)
        cent+=1
    return normalized #returns a list of 64x512 normalized images


In [15]:
#Iris Matching and Dimensionality Reduction
import cv2
import numpy as np
import glob
import math
from scipy.spatial import distance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics

def dim_reduction(feature_vector_train,feature_vector_test,components):
    '''TRAINING'''
    ft_train=feature_vector_train
    
    #get the classes of all training feature vectors
    y_train=[]
    for i in range(0,108):
        for k in range(0,3):
            y_train.append(i+1)
    y_train=np.array(y_train)
    
    #fit the LDA model on training data with n components
    sklearn_lda = LDA(n_components=components)
    sklearn_lda.fit(ft_train,y_train)
    
    #transform the traning data
    red_train=sklearn_lda.transform(ft_train)
    
    '''TESTING'''
    ft_test=feature_vector_test
    
    #transform the testing data
    red_test=sklearn_lda.transform(ft_test)
    
    
    #get a list of predicted values for the testing data to calculate ROC
    y_pred=sklearn_lda.predict(ft_test)
    
    #return transformed training and testing data, and the testing classes and predicted values for ROC
    return red_train,red_test


def IrisMatching(feature_vector_train,feature_vector_test,components,flag):
    
    #if flag is 1, we do not need to reduce dimesionality otherwise we call the dim_reduction function
    if flag==1:
        red_train=feature_vector_train
        red_test=feature_vector_test
        
    elif flag==0:
        red_train,red_test=dim_reduction(feature_vector_train,feature_vector_test,components)


    arr_f=red_test #test
    arr_fi=red_train #train
    
    index_L1=[]
    index_L2=[]
    index_cosine=[]
    min_cosine=[]
    
    #this loop iterates over each test image
    print("fts",len(feature_vector_train))
    print("fts2",len(feature_vector_test.shape))
    for i in range(0,len(arr_f)):
        L1=[]
        L2=[]
        Cosine=[]
        
        #this loop iterates over every training image - to be compared to each test image
        for j in range(0,len(arr_fi)):
            f=arr_f[i]
            fi=arr_fi[j]
            sumL1=0 #L1 distance
            sumL2=0 #L2 distance
            sumcos1=0
            sumcos2=0
            cosinedist=0 #cosine distance
            
            #calculate L1 and L2 using the formulas in the paper
            for l in range(0,len(f)):
                sumL1+=abs(f[l]-fi[l])
                sumL2+=math.pow((f[l]-fi[l]),2)
            
            
            #calculate sum of squares of all features for cosine distance
            for k in range(0,len(f)):
                sumcos1+=math.pow(f[k],2)
                sumcos2+=math.pow(fi[k],2)
                
            
            #calculate cosine distance using sumcos1 and sumcos2 calculated above
            cosinedist=1-((np.matmul(np.transpose(f),fi))/(math.pow(sumcos1,0.5)*math.pow(sumcos2,0.5)))
            
            L1.append(sumL1)
            L2.append(sumL2)
            Cosine.append(cosinedist)
        #get minimum values for L1 L2 and cosine distance for each test image and store their index
        index_L1.append(L1.index(min(L1)))
        index_L2.append(L2.index(min(L2)))
        index_cosine.append(Cosine.index(min(Cosine)))
        min_cosine.append(min(Cosine))
        
    match=0
    count=0
    
    #stores final matching - correct(1) or incorrect (0)
    match_L1=[]
    match_L2=[]
    match_cosine=[]
    match_cosine_ROC=[]
    
    #calculating matching of the test set according to the ROC thresholds
    thresh=[0.4,0.5,0.6]
    
    for x in range(0,len(thresh)):
        match_ROC=[]
        for y in range(0,len(min_cosine)):
            if min_cosine[y]<=thresh[x]:
                match_ROC.append(1)
            else:
                match_ROC.append(0)
        match_cosine_ROC.append(match_ROC)
        
    print("len l1:",len(index_L1))
    for k in range(0,len(index_L1)):
        '''count goes from 0 to 3 because we compare the indexes obtained for the first 4 images of the test data
        to the indexes of the first 3 images of 
        the train data (for which match is incremented by 3 everytime count exceeds the value of 3)'''
        if count<4:
            count+=1
        else:
            match+=3
            count=1
            
        '''check if matching is done correctly (1) or not (0) for L1 L2 and cosine distance and accordingly update
        the arrays match_L1,match_L2,match_cosine'''
        if index_L1[k] in range(match,match+3):
                match_L1.append(1)
        else:
            match_L1.append(0)
        if index_L2[k] in range(match,match+3):
            match_L2.append(1)
        else:
            match_L2.append(0)
        if index_cosine[k] in range(match,match+3):
            match_cosine.append(1)
        else:
            match_cosine.append(0)
    #reuturns the matching arrays, and test calsses and predicted values to calculate ROC
    return match_L1,match_L2,match_cosine,match_cosine_ROC



In [16]:
#Performance Evaluation
# coding: utf-8

import cv2
import numpy as np
import glob
import math
from scipy.spatial import distance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics

def PerformanceEvaluation(match_L1,match_L2,match_cosine):
    
    #storing only those elements that are correctly matched
    correct_L1 = [l for l in match_L1 if l==1]
    correct_L2 = [l for l in match_L2 if l==1]
    correct_cosine = [l for l in match_cosine if l==1]
    
    
    #calculating the correct recognition rates for L1,L2 and cosine similarity
    crr_L1=len(correct_L1)/len(match_L1)
    crr_L2=len(correct_L2)/len(match_L2)
    crr_cosine=len(correct_cosine)/len(match_cosine)
    
    
    return crr_L1*100,crr_L2*100,crr_cosine*100 #return CRR percentages

In [17]:
#Run the in/out of population test.
def IrisPopMatching(thresh,feature_vector_train,feature_vector_test,components,flag):
    
    #if flag is 1, we do not need to reduce dimesionality otherwise we call the dim_reduction function
    if flag==1:
        red_train=feature_vector_train
        red_test=feature_vector_test
        
    elif flag==0:
        red_train,red_test=dim_reduction(feature_vector_train,feature_vector_test,components)


    arr_f=red_test #test
    arr_fi=red_train #train
    
    index_L1=[]
    index_L2=[]
    index_cosine=[]
    min_cosine=[]
    
    #this loop iterates over each test image
    for i in range(0,len(arr_f)):
        L1=[]
        L2=[]
        Cosine=[]
        
        #this loop iterates over every training image in the population.
        #print(len(arr_fi))
        for j in range(0,int(len(arr_fi)/2)):
            f=arr_f[i]
            fi=arr_fi[j]
            sumL1=0 #L1 distance
            sumL2=0 #L2 distance
            sumcos1=0
            sumcos2=0
            cosinedist=0 #cosine distance
            
            #calculate L1 and L2 using the formulas in the paper
            for l in range(0,len(f)):
                sumL1+=abs(f[l]-fi[l])
                sumL2+=math.pow((f[l]-fi[l]),2)
            
            
            #calculate sum of squares of all features for cosine distance
            for k in range(0,len(f)):
                sumcos1+=math.pow(f[k],2)
                sumcos2+=math.pow(fi[k],2)
                
            
            #calculate cosine distance using sumcos1 and sumcos2 calculated above
            cosinedist=1-((np.matmul(np.transpose(f),fi))/(math.pow(sumcos1,0.5)*math.pow(sumcos2,0.5)))
            
            L1.append(sumL1)
            L2.append(sumL2)
            Cosine.append(cosinedist)
            
        #get minimum values for L1 L2 and cosine distance for each test image and store their index
        index_L1.append(L1.index(min(L1)))
        index_L2.append(L2.index(min(L2)))
        index_cosine.append(Cosine.index(min(Cosine)))
        min_cosine.append(min(Cosine))
        
    match=0
    count=0
    
    #stores final matching - correct(1) or incorrect (0)
    match_L1=[]
    match_L2=[]
    match_cosine=[]
    match_cosine_ROC=[]
    
    #In essence, we're taking every training image and comparing it to every test image. We take the cosinedist of
    #the comparison and append it to Cosine. We take the minimum of all training images when compared to the test image
    #and append it to the min_cosine and index_cosine arrays. 
    #We then iterate over our min_cosine array and see if the value is less than a certain threshold. If it is, then we
    #append a 1 to match_ROC, 0 else. 
    #MinCosine is length of all test irises and contains matches to all training ones. 
    
    for x in range(0,len(thresh)):
        match_ROC=[]
        for y in range(0,len(min_cosine)):
            if min_cosine[y]<=thresh[x]:
                match_ROC.append(y) #We believe that the match is person y.
            else:
                match_ROC.append(0) #We don't think anyone is a match.
        match_cosine_ROC.append(match_ROC) 
        
    
    for k in range(0,len(index_L1)):
        '''count goes from 0 to 3 because we compare the indexes obtained for the first 4 images of the test data
        to the indexes of the first 3 images of 
        the train data (for which match is incremented by 3 everytime count exceeds the value of 3)'''
        if count<4:
            count+=1
        else:
            match+=3
            count=1
            
        '''check if matching is done correctly (1) or not (0) for L1 L2 and cosine distance and accordingly update
        the arrays match_L1,match_L2,match_cosine'''
        if index_cosine[k] in range(match,match+3):
            match_cosine.append(k)
        else:
            match_cosine.append(0)
    #reuturns the matching arrays, and test calsses and predicted values to calculate ROC
    #print("MC:",match_cosine)
    #print("MCROC:",match_cosine_ROC)
    return match_cosine,match_cosine_ROC

In [10]:
#Process the training and testing data.
import cv2
import numpy as np
import glob
import math
import scipy
from scipy.spatial import distance
from scipy import signal
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
import matplotlib.pyplot as plt
import pandas as pd
from sklearn import metrics
import warnings
import os
warnings.filterwarnings("ignore")

#Training Data

#reading the training images from the CASIA dataset
os.chdir(r'/Users/Tory/Desktop/CASIA1/')
images_train = [cv2.imread(file) for file in sorted(glob.glob('*/*_1_*.jpg'))]
print(len(images_train))

#run Localization, Normalization,Enhancement and Feature Extraction on all the training images
boundary_train,centers_train=IrisLocalization(images_train)
normalized_train=IrisNormalization(boundary_train,centers_train)
enhanced_train=ImageEnhancement(normalized_train)
feature_vector_train=FeatureExtraction(enhanced_train)
print("Training data processed.")

#Testing Data

#reading the testing images from the CASIA dataset
os.chdir(r'/Users/Tory/Desktop/CASIA1/')
images_test = [cv2.imread(file) for file in sorted(glob.glob('*/*_2_*.jpg'))]

#run Localization, Normalization,Enhancement and Feature Extraction on all the testing images
boundary_test,centers_test=IrisLocalization(images_test)
normalized_test=IrisNormalization(boundary_test,centers_test)
enhanced_test=ImageEnhancement(normalized_test)
feature_vector_test=FeatureExtraction(enhanced_test)
print("Testing data processed.")


324
Training data processed.
Testing data processed.


In [9]:
#Compute the Error rates for various thresholds for the in/out population.
crr_L1=[]
crr_L2=[]
crr_cosine=[]
y_test=[]
y_pred=[]
match_cosine=[]
match_cosine_ROC=[]

#Only care about 107 dim. vector
components=[107]

print("Begin Matching test data with the train data")
thresh=[.4,.5,.55,0.6,.61,.62,.625,.63,.64,.65,0.7,0.8]

for comp in components:
    print(comp)
    
    #Running matching for all the dimensions specified in "components" 
    comp_match_cosine,comp_match_cosine_ROC=IrisPopMatching(thresh,feature_vector_train,feature_vector_test,comp,0)
    match_cosine.append(comp_match_cosine)
    match_cosine_ROC.append(comp_match_cosine_ROC)

for q in range(0,len(thresh)):
    u = match_cosine[0][:]
    v = match_cosine_ROC[0][q][:]
    #print("u",u)
    #print("v",v)
    falseNeg = 0
    falsePos = 0
    for i in range(len(v)):
        if i < len(v)/2:
            if v[i] != i:
                falseNeg += 1
        else:
            if v[i] != 0:
                falsePos += 1
    falseNeg = falseNeg/(len(v)/2)
    falsePos = falsePos/(len(v)/2)
    print("Threshold:",thresh[q],falseNeg,falsePos)

Begin Matching test data with the train data
107


NameError: name 'feature_vector_train' is not defined

In [19]:
#Run the in/out of population test.
def IrisIndividualMatching(thresh,feature_vector_train,feature_vector_test,components,flag):
    
    #if flag is 1, we do not need to reduce dimesionality otherwise we call the dim_reduction function
    if flag==1:
        red_train=feature_vector_train
        red_test=feature_vector_test
        
    elif flag==0:
        red_train,red_test=dim_reduction(feature_vector_train,feature_vector_test,components)


    arr_f=red_test #test
    arr_fi=red_train #train
    
    index_L1=[]
    index_L2=[]
    index_cosine=[]
    min_cosine=[]
    
    authentics = []
    imposters = []
    
    #this loop iterates over each test image
    print("lengths:",len(arr_f),len(arr_fi))
    for i in range(0,len(arr_f)):
        L1=[]
        L2=[]
        Cosine=[]
        
        #this loop iterates over every training image in the population.
        #print(len(arr_fi))
        for j in range(0,len(arr_fi)):
            f=arr_f[i]
            fi=arr_fi[j]
            sumL1=0 #L1 distance
            sumL2=0 #L2 distance
            sumcos1=0
            sumcos2=0
            cosinedist=0 #cosine distance
            
            #calculate L1 and L2 using the formulas in the paper
            for l in range(0,len(f)):
                sumL1+=abs(f[l]-fi[l])
                sumL2+=math.pow((f[l]-fi[l]),2)
            
            
            #calculate sum of squares of all features for cosine distance
            for k in range(0,len(f)):
                sumcos1+=math.pow(f[k],2)
                sumcos2+=math.pow(fi[k],2)
                
            
            #calculate cosine distance using sumcos1 and sumcos2 calculated above
            cosinedist=1-((np.matmul(np.transpose(f),fi))/(math.pow(sumcos1,0.5)*math.pow(sumcos2,0.5)))
            
            L1.append(sumL1)
            L2.append(sumL2)
            Cosine.append(cosinedist)
            #print(i,j)
            if int(i/4) == int(j/3):
                authentics.append(cosinedist)
                #print("authentic ",cosinedist)
            else:
                imposters.append(cosinedist)
                #print("imp",cosinedist)

            
        #get minimum values for L1 L2 and cosine distance for each test image and store their index
        index_L1.append(L1.index(min(L1)))
        index_L2.append(L2.index(min(L2)))
        index_cosine.append(Cosine.index(min(Cosine)))
        min_cosine.append(min(Cosine))
        
    match=0
    count=0
    
    #stores final matching - correct(1) or incorrect (0)
    match_L1=[]
    match_L2=[]
    match_cosine=[]
    match_cosine_ROC=[]
    
    #In essence, we're taking every training image and comparing it to every test image. We take the cosinedist of
    #the comparison and append it to Cosine. We take the minimum of all training images when compared to the test image
    #and append it to the min_cosine and index_cosine arrays. 
    #We then iterate over our min_cosine array and see if the value is less than a certain threshold. If it is, then we
    #append a 1 to match_ROC, 0 else. 
    #MinCosine is length of all test irises and contains matches to all training ones. 
    print("Authentics:",np.mean(authentics))
    print("Imposters:",np.mean(imposters))
    
    for x in range(0,len(thresh)):
        match_ROC=[]
        for y in range(0,len(min_cosine)):
            if min_cosine[y]<=thresh[x]:
                match_ROC.append(y) #We believe that the match is person y.
            else:
                match_ROC.append(0) #We don't think anyone is a match.
        match_cosine_ROC.append(match_ROC) 
        
    
    for k in range(0,len(index_L1)):
        '''count goes from 0 to 3 because we compare the indexes obtained for the first 4 images of the test data
        to the indexes of the first 3 images of 
        the train data (for which match is incremented by 3 everytime count exceeds the value of 3)'''
        if count<4:
            count+=1
        else:
            match+=3
            count=1
            
        '''check if matching is done correctly (1) or not (0) for L1 L2 and cosine distance and accordingly update
        the arrays match_L1,match_L2,match_cosine'''
        if index_cosine[k] in range(match,match+3):
            match_cosine.append(k)
        else:
            match_cosine.append(0)
    #reuturns the matching arrays, and test calsses and predicted values to calculate ROC
    #print("MC:",match_cosine)
    #print("MCROC:",match_cosine_ROC)
    return authentics,imposters

In [20]:
#Run for analysis of error for singular comparisons.
crr_L1=[]
crr_L2=[]
crr_cosine=[]
y_test=[]
y_pred=[]
match_cosine=[]
match_cosine_ROC=[]

#Only care about 107 dim. vector
components=[107]

print("Begin Matching test data with the train data")
thresh=[.82,.83,.84,.85,.86,.87,.88,.89,.90,.91,.92,.93,.94,.95,.96,.97,.98,.99]

authentics,imposters=IrisIndividualMatching(thresh,feature_vector_train,feature_vector_test,components[0],0)
    
for q in range(0,len(thresh)):
    falseNeg = 0
    falsePos = 0
    for i in range(len(authentics)):
        if authentics[i] > thresh[q]:
            falseNeg += 1
    for i in range(len(imposters)):
        if imposters[i] < thresh[q]:
            falsePos += 1  
    falseNeg = falseNeg/(len(authentics))
    falsePos = falsePos/(len(imposters))
    print("Threshold:",thresh[q],falseNeg,falsePos)
    
print("Authentics")
for i in range(len(authentics)):
    print(authentics[i])
print("Imposters")
for i in range(len(imposters)):
    print(imposters[i])

Begin Matching test data with the train data
lengths: 432 324
Authentics: 0.6274221538264119
Imposters: 1.0033541175667593
Threshold: 0.82 0.14814814814814814 0.06739644629052728
Threshold: 0.83 0.13503086419753085 0.07808353524864428
Threshold: 0.84 0.125 0.08941963770624206
Threshold: 0.85 0.11419753086419752 0.10210424599053883
Threshold: 0.86 0.10416666666666667 0.11724789431175724
Threshold: 0.87 0.09645061728395062 0.13358861197646243
Threshold: 0.88 0.08487654320987655 0.15085237106265142
Threshold: 0.89 0.08024691358024691 0.17044536748586592
Threshold: 0.9 0.07253086419753087 0.19160320756893964
Threshold: 0.91 0.06404320987654322 0.21360476520133842
Threshold: 0.92 0.05864197530864197 0.23770479981539172
Threshold: 0.93 0.05478395061728395 0.2633047767393562
Threshold: 0.94 0.04861111111111111 0.2900946117457021
Threshold: 0.95 0.04552469135802469 0.31873774085612094
Threshold: 0.96 0.03780864197530864 0.348693319487712
Threshold: 0.97 0.036265432098765434 0.3794709818853121


1.0484044987021364
0.9679724243857549
0.951854053298989
1.0294610185548374
1.143161108194069
1.157181562301255
1.2182275745530462
1.0865082412646376
0.943508784265379
1.2049106942068115
1.1541111806708715
1.1090241375561711
1.0968267793136424
0.8822139276378121
0.9361313927863756
0.8896024326921659
0.8321805065036811
0.8163639528532651
0.7201524885532362
1.0253485240108249
1.1042625860935338
0.9896986123666364
0.736043525921384
0.8159246416751137
0.7826905447348941
1.139626487460772
1.0038635817597965
1.1351070443009044
0.6515893498534282
0.8043725172027021
0.6935935284584573
1.1337668330681916
1.09181835711882
1.1758948820406836
0.9834318988924852
0.9951785277946921
1.0534816095690847
0.9613476972038822
0.8327645045444939
0.9085629885667988
0.8443524300138956
0.9140166628993388
0.8328833392197279
0.8970522121422345
0.8451630099400221
0.8689734011691103
1.0890236710671475
0.8262271430800727
0.7661055924492215
1.1010592152937695
0.9672266944712418
0.9132345504227979
0.8516643041562757
0

1.065929061725885
1.045199891572838
0.9050976850722185
0.734459965650287
0.7685505485211003
0.8086392043076283
1.0339951780133059
0.9499619717767475
0.90562291490162
1.2406841077068667
1.2880004784326242
1.1443132125878794
1.0146973928288088
1.1507641139182003
1.1741677641148391
0.7383966142670019
0.9522575599809117
0.813069487000079
1.1698793957789184
1.195726840127256
1.167504238557569
1.0319313897026678
0.9783433664990623
1.0245813445315521
0.8626158070207283
1.0371867032515358
0.8191860493657401
1.0413257568017649
1.0612217982754228
1.0532672751173362
0.9400518142548998
0.9948378306839261
0.9596010913679304
1.1241783210061946
1.076823393574698
1.0712148161005461
0.9570579333456406
0.828925865400731
0.847737330499509
0.9488936184731158
0.9416734115556078
1.011526931157665
1.0280821833450382
1.0176326949526353
0.9634918629544834
0.7408240654278082
0.721472982059383
0.7957228745262349
0.789058756866315
0.8071253757320412
0.8200631617389488
0.947424921911165
0.900562015323293
0.7343496

1.0557511137776432
1.0509586994728424
0.9397315015953073
0.6916352549976449
0.9767143187659811
0.9830313272175814
1.2054416253643891
1.204481377567976
1.1764638593250596
1.1023049979175585
1.137516843664666
1.1145479144577424
0.880741035450588
0.918753269095027
0.9089264658792855
1.2075538317666674
1.2626794373971264
1.1967273338427127
0.9312313969604037
0.9934984311230088
0.8222080230705763
0.8388808044355889
0.876271329483907
0.8491277889804353
0.9533954527828595
0.9238956435199723
1.0287119495932093
0.923846535895498
1.0059386249072888
0.7428333493741156
0.8167142143272291
0.8620342988430415
1.1048630817222747
1.1106275813540158
1.2376371147914003
1.1559880061798595
0.89235695043517
1.0414879610031913
0.9345550330927674
1.0030387686906497
0.9939010780199841
1.0228079054929573
1.0525799212101186
1.1296910477130864
1.0955294825308486
1.1021407280044524
1.088839474337383
1.1570818612852896
1.041163543166444
1.1404391348055434
1.0417690439651166
0.9328769119551072
0.9605219733739931
1.0

1.0550828707970785
1.0488823502770068
1.0978239632469566
1.0278323620949545
0.9807810798524391
1.0944085229830531
0.8961347574468419
0.8073229725266496
0.9138525204340332
1.1659423588091022
1.085160292728445
1.0328524454660308
0.940171747100979
0.928177851201418
0.9793026906591975
0.962075924316869
1.048456445687072
1.1118762343753905
0.9870213693199614
0.982208640871672
0.8929565193163286
0.9212377705418314
0.7939513816022105
1.0474164240975696
1.0924812638247217
0.9752063832059118
1.04957841659354
1.0229538380292387
0.946875023060077
0.9724153236900254
1.011693343418311
1.04618463938639
1.1460895324957083
1.131808683509546
1.061822966197616
0.9176434447673993
0.8865063753593536
0.87151405587467
0.9371467303058417
1.1629221806507304
0.9837619101582382
0.9144579941313576
0.8633750673494205
1.000872160457615
0.9795174857083233
1.0693092520780534
0.9767495486360851
0.9729288228502891
1.0822426310035205
1.0863196566431517
0.9465247397721249
0.796480398672897
1.0521100836209996
1.088976544

...

0.8438674568666482
0.9575161357820894
1.0990693488561996
1.1026529391752127
1.1213136368549295
1.051073328868528
1.0403847220517155
0.923114809434244
1.0500411747795817
0.8699509574807068
0.8014119719112838
1.0382851694177617
1.372830884416127
1.1533959682368486
1.0025714828121175
1.0566148587284456
0.9724275649702939
0.8903953554890135
0.7252058668521884
0.6456537949642028
0.9565285361840006
0.7777126869358028
0.9710395559627838
1.0817707719818976
0.9260363811741512
0.9405285945377091
0.918194531079187
1.0832054005740894
1.0672522373238
0.9443317924771907
1.0329067649104111
1.0683844410614947
0.964532421278394
0.8631378205261957
0.9409168126732353
0.894086680536555
0.9090362646813523
0.8516352032938954
1.0948789781044264
1.054581867950079
1.0487669184394808
0.8678601777877087
0.9348000444056054
0.9053355570076493
0.873275636257712
1.035356057884573
0.8501849023138477
1.1800272070976103
1.0469941782129484
1.1294201101955357
1.1049770657493807
0.9735125027617721
0.9088432707922294
1.025

0.676651387101933
0.8285677043655392
0.9712037509764442
1.0009095098112049
0.8372821976620621
1.1142000271935777
1.1436111154158985
1.0057709168766884
0.7802335684483599
0.7755072391606672
0.7017564662327358
1.0445942890927153
0.8652916428809678
0.8884002052286567
0.9480639018194932
1.0919809620795788
0.7936197136081429
0.8009369517056264
0.7731275486295939
0.7077983453172463
0.961055492164106
0.9305570761693147
0.7741873988615566
1.117032137104067
1.194939817897811
1.1941370385843229
0.9205906631891183
0.9212166376379325
0.9013780537001115
1.1002230679547258
1.0040554398724095
1.1289809163920577
0.9235455869168397
0.8349755661743805
0.8547111577905828
1.032983045189662
1.1012393457091343
1.084916150885793
0.8721909326279617
0.8702090370345834
0.7802385493350836
0.899244529639517
0.922291952785489
0.928085266591375
0.8174794086138196
0.8758602995326241
0.9297811575626862
1.1128185286327785
1.1567466871597607
1.1686879902188196
0.7876940468968445
0.9182756268048521
0.8192040094075953
0.

1.1308937174021079
1.0595192181380144
0.9345499702401094
1.069016537485435
1.0192370926152305
1.0805014521151346
1.016129802163221
1.193898154589339
1.1866976839426355
1.0467046564491405
0.9271327337047406
1.0572159769409373
0.817315623698667
0.8016564060600382
0.8529781320787101
0.8840118021015094
0.9106585172150734
0.9026912237452113
0.8913925843826933
0.8989163815971921
0.9493110670943481
1.0620061359717157
1.1724651832210846
0.9322834793488007
1.1374264697504872
0.9913170352140157
0.983774315942305
0.7914307005845139
0.8533656039074115
1.035577890491985
0.906725676219914
0.9033878322272633
0.8448060516298826
0.9839648278506609
1.0628557946312973
1.0188195223124126
0.766211342739435
0.6823269580915852
0.7433452951345414
1.0193675202176957
1.0993280991146959
0.9997679831000555
1.0602758955366838
0.9372977986257265
1.0551363681013448
1.24041025299888
1.1999179824490758
1.1659823374210316
1.225054389116467
1.0926583811713146
0.9726928725007747
0.9853738674882901
0.7561499239655951
0.96

0.9324720164338384
0.8172363055448737
0.9047240719212477
0.8597102662502363
0.8643207100884156
1.1361826430820847
1.1012332717093882
1.0857121665477747
1.0739365254800965
0.9520992679380138
0.9646386254813079
0.9842014789520851
0.9871825409117161
0.9912914477712254
0.8348767824580262
0.8629952793908203
0.8953367842261879
1.016265571688287
0.7036675610743235
0.827190935618415
1.2742665370739468
1.2040831476832026
1.311153455681973
0.9801422949446591
1.001587122251144
1.0682584813565266
0.8700700860395114
0.8643163650210504
0.8004725794151544
1.2295556111494745
0.8982291790973947
1.121834294468533
0.8515316693522073
0.7766229804402951
1.0172434309054879
1.0296564214146984
0.9852756620404721
1.0913863054871589
0.948003088902348
1.0428280978915452
1.0187991597981556
0.8186986604062949
0.9648488381346169
1.0368212831689911
1.142565192059414
1.1348348839548472
1.1088388149711703
1.08531062121539
1.017131092922712
1.1859000284871568
0.8881668749444788
1.00657592709264
0.9293181072059391
1.025

0.9383183735653813
0.9992712442471554
1.0281322197116838
1.0135663703902387
0.9829464309548317
1.0587236073690258
1.1230929909613108
1.0509684823184664
0.9899985301367179
1.0984568173208573
1.0414602296626672
1.1618725609265337
1.0944845059183979
0.8028918647860732
0.7890669236050286
0.8690222253447349
1.0539124438635004
1.1146779310083303
1.2462465117313917
1.0441272585578107
1.0657422416415347
1.0705684746870419
0.8553155933622969
0.8830209306626728
0.8617342198051591
1.0428233060028107
0.9559938479225207
0.9630777763075411
0.8266031989414551
0.9136123195936476
0.8827533808015533
0.9693316331053775
1.0926584771117016
1.055311533642237
1.1313484136611736
1.13392973375823
1.1143397428035906
1.0911407968031304
1.235781077654136
1.1562079083498955
0.9645064668024161
1.0994958143790745
0.9511401540540245
0.876248313855444
1.0057768586118156
1.0420896349557622
0.9131093573175656
0.8361263486142888
0.7813479003341322
0.9587246740353893
0.8919365916990021
0.8041814767592059
0.661928979267114